<a href="https://colab.research.google.com/github/supai-red/DS-Unit-2-Regression-Classification/blob/master/DS7_212_Andrea_Christelle__assignment_regression_classification_2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Lambda School Data Science, Unit 2: Predictive Modeling

# Regression & Classification, Module 2

## Assignment

You'll continue to **predict how much it costs to rent an apartment in NYC,** using the dataset from renthop.com.

- [X ] Do train/test split. Use data from April & May 2016 to train. Use data from June 2016 to test.
- [x ] Engineer at least two new features. (See below for explanation & ideas.)
- [X] Fit a linear regression model with at least two features.
- [X] Get the model's coefficients and intercept.
- [X] Get regression metrics RMSE, MAE, and $R^2$, for both the train and test data.
- [ ] What's the best test MAE you can get? Share your score and features used with your cohort on Slack!
- [ ] As always, commit your notebook to your fork of the GitHub repo.


#### [Feature Engineering](https://en.wikipedia.org/wiki/Feature_engineering)

> "Some machine learning projects succeed and some fail. What makes the difference? Easily the most important factor is the features used." — Pedro Domingos, ["A Few Useful Things to Know about Machine Learning"](https://homes.cs.washington.edu/~pedrod/papers/cacm12.pdf)

> "Coming up with features is difficult, time-consuming, requires expert knowledge. 'Applied machine learning' is basically feature engineering." — Andrew Ng, [Machine Learning and AI via Brain simulations](https://forum.stanford.edu/events/2011/2011slides/plenary/2011plenaryNg.pdf) 

> Feature engineering is the process of using domain knowledge of the data to create features that make machine learning algorithms work. 

#### Feature Ideas
- Does the apartment have a description?
- How long is the description?
- How many total perks does each apartment have?
- Are cats _or_ dogs allowed?
- Are cats _and_ dogs allowed?
- Total number of rooms (beds + baths)
- Ratio of beds to baths
- What's the neighborhood, based on address or latitude & longitude?

## Stretch Goals
- [ ] If you want more math, skim [_An Introduction to Statistical Learning_](http://faculty.marshall.usc.edu/gareth-james/ISL/ISLR%20Seventh%20Printing.pdf),  Chapter 3.1, Simple Linear Regression, & Chapter 3.2, Multiple Linear Regression
- [ ] If you want more introduction, watch [Brandon Foltz, Statistics 101: Simple Linear Regression](https://www.youtube.com/watch?v=ZkjP5RJLQF4)
(20 minutes, over 1 million views)
- [ ] Do the [Plotly Dash](https://dash.plot.ly/) Tutorial, Parts 1 & 2.
- [ ] Add your own stretch goal(s) !

In [3]:
# If you're in Colab...
import os, sys
in_colab = 'google.colab' in sys.modules

if in_colab:
    # Install required python packages:
    # pandas-profiling, version >= 2.0
    # plotly, version >= 4.0
    !pip install --upgrade pandas-profiling plotly
    
    # Pull files from Github repo
    os.chdir('/content')
    !git init .
    !git remote add origin https://github.com/LambdaSchool/DS-Unit-2-Regression-Classification.git
    !git pull origin master
    
    # Change into directory for module
    os.chdir('module1')

Requirement already up-to-date: pandas-profiling in /usr/local/lib/python3.6/dist-packages (2.3.0)
Requirement already up-to-date: plotly in /usr/local/lib/python3.6/dist-packages (4.1.1)
Reinitialized existing Git repository in /content/.git/
fatal: remote origin already exists.
From https://github.com/LambdaSchool/DS-Unit-2-Regression-Classification
 * branch            master     -> FETCH_HEAD
Already up to date.


In [0]:
# Ignore this Numpy warning when using Plotly Express:
# FutureWarning: Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.
import warnings
warnings.filterwarnings(action='ignore', category=FutureWarning, module='numpy')

In [0]:
import numpy as np
import pandas as pd

# Read New York City apartment rental listing data
df = pd.read_csv('../data/renthop-nyc.csv')
assert df.shape == (49352, 34)

# Remove the most extreme 1% prices,
# the most extreme .1% latitudes, &
# the most extreme .1% longitudes
df = df[(df['price'] >= np.percentile(df['price'], 0.5)) & 
        (df['price'] <= np.percentile(df['price'], 99.5)) & 
        (df['latitude'] >= np.percentile(df['latitude'], 0.05)) & 
        (df['latitude'] < np.percentile(df['latitude'], 99.95)) &
        (df['longitude'] >= np.percentile(df['longitude'], 0.05)) & 
        (df['longitude'] <= np.percentile(df['longitude'], 99.95))]

###Train/Test split. 
Using data from April & May 2016 to train.
Using data from june 2016 to test.

In [6]:
#Note: outliers have been removed in code above
print(df.shape)
#Reduced instances by 835
df.head()

(48817, 34)


bathrooms  bedrooms  ... wheelchair_access common_outdoor_space
0        1.5         3  ...                 0                    0
1        1.0         2  ...                 0                    0
2        1.0         1  ...                 0                    0
3        1.0         1  ...                 0                    0
4        1.0         4  ...                 0                    0

[5 rows x 34 columns]

In [7]:
#CHANGE COLUMN NAMES. Replace spaces with underscores
df.columns = [col.replace(' ', '_') for col in df]
df.head()

bathrooms  bedrooms  ... wheelchair_access common_outdoor_space
0        1.5         3  ...                 0                    0
1        1.0         2  ...                 0                    0
2        1.0         1  ...                 0                    0
3        1.0         1  ...                 0                    0
4        1.0         4  ...                 0                    0

[5 rows x 34 columns]

In [8]:
#ADD COMMAS to PRICE
df['price'].dtype
#price is an integer

pd.options.display.float_format = '{:,}'.format
df.head()
##########NOT WORKING TO ADD COMMAS

bathrooms  bedrooms  ... wheelchair_access common_outdoor_space
0        1.5         3  ...                 0                    0
1        1.0         2  ...                 0                    0
2        1.0         1  ...                 0                    0
3        1.0         1  ...                 0                    0
4        1.0         4  ...                 0                    0

[5 rows x 34 columns]

In [9]:
df.dtypes

bathrooms               float64
bedrooms                  int64
created                  object
description              object
display_address          object
latitude                float64
longitude               float64
price                     int64
street_address           object
interest_level           object
elevator                  int64
cats_allowed              int64
hardwood_floors           int64
dogs_allowed              int64
doorman                   int64
dishwasher                int64
no_fee                    int64
laundry_in_building       int64
fitness_center            int64
pre-war                   int64
laundry_in_unit           int64
roof_deck                 int64
outdoor_space             int64
dining_room               int64
high_speed_internet       int64
balcony                   int64
swimming_pool             int64
new_construction          int64
terrace                   int64
exclusive                 int64
loft                      int64
garden_p

In [10]:
#Change "created" into date/time format
df['created'] = pd.to_datetime(df['created'], infer_datetime_format=True)

df.head()
df['created'].dtypes
df['created'].describe()

count                   48817
unique                  48148
top       2016-05-14 01:11:03
freq                        3
first     2016-04-01 22:12:41
last      2016-06-29 21:41:47
Name: created, dtype: object

In [11]:
df['created'].dt.month.value_counts()

#Gives number of values in data frame per month

6    16973
4    16217
5    15627
Name: created, dtype: int64

In [12]:
df['interest_level'].value_counts()

low       33946
medium    11181
high       3690
Name: interest_level, dtype: int64

###Some alternatives for separating the data

In [40]:
#GET SUBSET OF DATA FROM APRIL and MAY - my method
#April May to Train
#June to Test
# df['created'].head()

mask = (df['created'] > '2016-04-01') & (df['created'] <= '2016-05-31')
train = df[mask]
train.shape

mask2 = (df['created'] > '2016-06-01') & (df['created'] <= '2016-06-30')
test = df[mask2]
test.shape

train.shape, test.shape

((31839, 34), (16973, 34))

In [0]:
#Establish X as a pd DF (or matrix), establish y as a pd Series (or vector)
#First pull the target (y) out of the original dataframe
#Second drop the target from the features matrix (X)
#This is an example of how you would get a target and features generally
#Below we do the same on two narrowed data sets

y = df['price']
X = df.drop('price', axis=1)
print(y.head())
print(X.head())

In [0]:
##Filtering train and test sets based on dates
y_train = train['price']
y_test = test['price']

X_train = train.drop('price', axis=1)
X_test = train.drop('price', axis=1)

In [0]:
#from Johana original 
# pd.Timestamp(year=2016, month=4, day=1)
# train_data=df[(df['created']>= pd.Timestamp(year=2016, month=4, day=1))&(df['created']< pd.Timestamp(year=2016, month=6, day=1))] 
# test_data=df[(df['created']>= pd.Timestamp(year=2016, month=6, day=1))]


In [0]:
print(train.head())

In [0]:
print(test.head())

###Explore and clean data

###Warning: bedrooms has 6172 (19.4% zeros)
Should we handle zeros like missing / null values?
Why are bedrooms missing almost 20% of the time? These are probably studios or lofts.

In [0]:
#Treat zeros like null values.
#Advised to replace in both sets with mean from the training set

#train['bedrooms'] = train['bedrooms'].replace(0, train['bedrooms'].mean())
#test['bedrooms'] = test['bedrooms'].replace(0, test['bedrooms'].mean())

#I might do this if these were empty, but 0 may well indicate 0.
#In NYC I think 0 bedrooms indicates a studio or loft.

# Do Train/Test Split

In [0]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=11)

#Engineer new features

In [66]:
#Look at relationship between location & price
import plotly.express as px

px.scatter(train, x = 'longitude', y = 'latitude', color='price', opacity = 0.5)

#OOOOOH, look how you can pick any feature as a scale for color! Bedrooms, cats_allowed, anything works

In [67]:
#Cluster the locations
from sklearn.cluster import KMeans
kmeans = KMeans(n_clusters=10, n_jobs = -1)
train['cluster'] = kmeans.fit_predict(train[['longitude', 'latitude']])
test['cluster'] = kmeans.predict(test[['longitude', 'latitude']])
px.scatter(train, x='longitude', y='latitude', color='cluster')

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy



In [0]:
KMeans?

In [50]:
def engingeer_features(df):
  #What's the neighborhood, based on address or latitude & longitude
  clusters = pd.get_dummies(df['cluster'], prefix='cluster')
  for col in clusters:
    df[col] = clusters[col]
    
  #Encode the interest level
  interest_level = pd.get_dummies(df['interest_level'], prefix='interest_level')
  for col in interest_level:
    df[col] = interest_level[col]
    
  #Does the apartment have a description?
  df['description'] = df['description'].str.strip().fillna('')
  df['has_description'] = df['description'] != ''
  
  #How long is the description?
  df['description_length'] = df['description'].str.len()
  
  
#How many total perks does each apartment have?
  perk_cols = ['elevator', 'cats_allowed', 'hardwood_floors', 'dogs_allowed',
                 'doorman', 'dishwasher', 'no_fee', 'laundry_in_building',
                 'fitness_center', 'pre-war', 'laundry_in_unit', 'roof_deck',
                 'outdoor_space', 'dining_room', 'high_speed_internet', 'balcony',
                 'swimming_pool', 'new_construction', 'exclusive', 'terrace', 
                 'loft', 'garden_patio', 'common_outdoor_space', 
                 'wheelchair_access']
  df['perk_count'] = df[perk_cols].sum(axis=1)
  
      # Are cats or dogs allowed?
  df['cats_or_dogs'] = (df['cats_allowed']==1) | (df['dogs_allowed']==1)

    # Are cats and dogs allowed?
  df['cats_and_dogs'] = (df['cats_allowed']==1) & (df['dogs_allowed']==1)

    # Total number of rooms (beds + baths)
  df['rooms'] = df['bedrooms'] + df['bathrooms']

    # Ratio of baths to beds
  df['ratio_baths_beds'] =  df['bathrooms'] / df['bedrooms']
    
    #Lots of outdoors
  df['outdoors'] = (df['garden_patio']==1) & (df['common_outdoor_space'] == 1)
    
  return df

train = engingeer_features(train)
test = engingeer_features(test)
train.shape, test.shape  
  

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:13: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-

((31839, 56), (16973, 56))

In [68]:
import pandas_profiling
train.profile_report()

###Mean baseline

In [69]:
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

y_train = train['price']
y_test = test['price']
y_pred_train = [y_train.mean()] * len(y_train)
y_pred_test = [y_train.mean()] * len(y_test)

print('Mean Baseline:')
print('Train Root Mean Squared Error:', np.sqrt(mean_squared_error(y_train, y_pred_train)))
print('Test Root Mean Square Error:', np.sqrt(mean_squared_error(y_test, y_pred_test)))
print('Train Mean Absolute Error:', mean_absolute_error(y_train, y_pred_train))
print('Test Mean Absolute Error:', mean_absolute_error(y_test, y_pred_test))
print('Train R^2 Score:', r2_score(y_train, y_pred_train))
print('Test R^2 Score:', r2_score(y_test, y_pred_test))

Mean Baseline:
Train Root Mean Squared Error: 1762.2054928073617
Test Root Mean Square Error: 1762.9944244959047
Train Mean Absolute Error: 1201.9731808995773
Test Mean Absolute Error: 1197.7457387676025
Train R^2 Score: 0.0
Test R^2 Score: -4.120723124012571e-05


##Fit a linear regression model


*   with at least two features
*   Get the model's coefficients and intercept
*   Get regression metrics RMSE, MAE, and R^2, for boht the train and test data



In [0]:
from sklearn.linear_model import LinearRegression

def lr(train, test, features, target):
    X_train = train[features]
    y_train = train[target]
    X_test = test[features]
    y_test = test[target]

    model = LinearRegression()
    model.fit(X_train, y_train)
    y_pred_train = model.predict(X_train)
    y_pred_test = model.predict(X_test)
    
    print(f'Linear Regression with {len(features)} features')
    print('Intercept', model.intercept_)
    coefficients = pd.Series(model.coef_, features)
    print(coefficients.to_string())
    
    print('Train Root Mean Squared Error:', np.sqrt(mean_squared_error(y_train, y_pred_train)))
    print('Test Root Mean Square Error:', np.sqrt(mean_squared_error(y_test, y_pred_test)))
    print('Train Mean Absolute Error:', mean_absolute_error(y_train, y_pred_train))
    print('Test Mean Absolute Error:', mean_absolute_error(y_test, y_pred_test))
    print('Train R^2 Score:', r2_score(y_train, y_pred_train))
    print('Test R^2 Score:', r2_score(y_test, y_pred_test))


In [73]:
target = 'price'
features = ['garden_patio', 'bathrooms']
lr(train, test, features, target)

Linear Regression with 2 features
Intercept 505.71406495230303
garden_patio     278.1559986602401
bathrooms      2,541.2982412601455
Train Root Mean Squared Error: 1284.1558213532678
Test Root Mean Square Error: 1268.2223823747079
Train Mean Absolute Error: 887.0688328949891
Test Mean Absolute Error: 888.693321489884
Train R^2 Score: 0.4689659750782492
Test R^2 Score: 0.4825041811031525


In [74]:
features = ['bedrooms', 'bathrooms', 'longitude', 'perk_count']
lr(train, test, features, target)

Linear Regression with 4 features
Intercept -1042396.7102589727
bedrooms        424.6423159961095
bathrooms      1,932.542432122309
longitude    -14,096.752174539883
perk_count       46.7075924371934
Train Root Mean Squared Error: 1138.2699385051906
Test Root Mean Square Error: 1124.6118344013216
Train Mean Absolute Error: 727.0542451204832
Test Mean Absolute Error: 732.2101476171129
Train R^2 Score: 0.5827681711393427
Test R^2 Score: 0.5930684930771513


In [0]:
and keep testing


###Perform random train/test split
##For random state



In [0]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=11)

In [0]:
X_train.head()

In [0]:
X_test.head()

In [0]:
y_train.head()

In [0]:
y_test.head()

Repeatedly fit increasingly complex models, and keep track of the scores.

In [0]:
from IPython.display import display, HTML
from sklearn.linear_model import LinearRegression
from sklearn.metrics import r2_score
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import LinearRegression

In [0]:
import matplotlib.pyplot as plt

#Credit Ryan Herr crediting Jake VanderPlas

def PolynomialRegression(degree=2, **kwargs):
  return make_pipeline(PolynomialFeatures(degree),
                       LinearRegression(**kwargs))

polynomial_degrees = range(1, 100, 25)
train_r2s = []
test_r2s = []

for degree in polynomial_degrees:
  model = PolynomialRegression(degree)
  display(HTML(f'Polynomial degree={degree}'))
  
  model.fit(X_train, y_train)
  train_r2 = model.score(X_train, y_train)
  test_r2 = model.score(X_test, y_test)
  display(HTML(f'<b style="color: blue">Train R2 {train_r2:.2f}</b'))
  display(HTML(f'<b style="color: red">Test R2 {test_r2:.2f}</b>'))
  
  plt.scatter(X_train, y_train, color ='blue', alpha=0.5)
  plt.scatter(X_test, y_test, color='red', alpha=0.5)
  plt.xlabel(features)
  plt.ylabel(target)
  
  x_domain = np.linspace(X.min(), X.max())
  curve = model.predict(x_domain)
  plt.plot(x_domain, curve, color="blue")
  #plt.show()pl
  display(HTML('<hr/>'))
  
  train_r2s.append(train_r2)
  test_r2s.append(test_r2)
  
display(HTML('Validation Curve'))
plt.plot(polynomial_degrees, train_r2s, color='blue', label='Train')
plt.plot(polynomial_degrees, test_r2s, color='red', label='Test')
plt.xlabel('Model Complexity (Polynomial Degree)')
plt.ylabel('R^2 Score') 
plt.legend()
plt.show()